In [49]:
function accuracy()
    ac=700;
    return ac;
end
setprecision(accuracy());

In [50]:
function order()
    M=10;
    return M+1;
end

order (generic function with 1 method)

In [51]:
function steps()
    h = BigFloat(1)/BigFloat(100)
    return h;
end

steps (generic function with 1 method)

In [52]:
function JCh(k,i)
     
    k = BigFloat(k);
    i = BigFloat(i);
    s = BigFloat(1);
    if i < k/2
        i = k - i;
    end
    for j in range(k,i+1,step=-1)
        
        j1=BigFloat(j)
        s = s*j1/(j1-i)
        
    end
    
    return s
end

JCh (generic function with 1 method)

In [53]:
function DJCh()
    Cki = Array{BigFloat}(undef,order()-1,order()-1);
    for k in 1:order()-1
        for j in 1:k
            Cki[k,j] = 1
        end
    end
    
    for k in 2:order()-2
        for i in 1:k-1
           Cki[k+1,i+1] = Cki[k,i] + Cki[k,i+1]
        end
    end
    return Cki
end

DJCh (generic function with 1 method)

In [54]:
function multi()
    S = Array{BigFloat}(undef,1,order());
    S[1] = BigFloat(1)
    
    for i in 1:order()-1
        S[i+1] = S[i]*steps()/BigFloat(i)
    end
    
    return S
end

multi (generic function with 1 method)

In [55]:
fdot1(x,y,z) = @. x*y*z
fdot2(x,y) = @. x*y
function Sumxyz1(x,y,Cki)
    return sum(fdot1(Cki[1:end],reverse!(x[1:end]),y[1:end]))
end 
function Sumxyz2(x,y,Cki)
    return sum(fdot2(Cki,fdot2(reverse!(x[1:end]),x[1:end]) .- fdot2(reverse!(y[1:end]),y[1:end])))
end 

Sumxyz2 (generic function with 1 method)

In [56]:
fdot1(x,y,z) = @. x*y*z
fdot2(x,y) = @. x*y
function Sumuvw1(x,y,u,v,Cki)
    return sum(fdot1(Cki[1:end],reverse!(x[1:end]),v[1:end])) + sum(fdot1(Cki[1:end],reverse!(y[1:end]),u[1:end]))
end 
function Sumuvw2(x,y,u,v,Cki)
    return sum(fdot2(Cki,fdot2(reverse!(x[1:end]),u[1:end]) .- fdot2(reverse!(y[1:end]),v[1:end]))) + sum(fdot2(Cki,fdot2(reverse!(u[1:end]),x[1:end]) .- fdot2(reverse!(v[1:end]),y[1:end])))
end 

Sumuvw2 (generic function with 1 method)

In [57]:
function Talor(x,y,u,v,Cki)
    for k in 1:order()-2
        x[k+2] = -x[k] - BigFloat(2)*Sumxyz1(x[1:k],y[1:k],Cki[k,1:k])
        y[k+2] = -y[k] - Sumxyz2(x[1:k],y[1:k],Cki[k,1:k])
        
    end
    
    for k in 1:order()-2
        u[k+2] = -u[k] - BigFloat(2)*Sumuvw1(x[1:k],y[1:k],u[1:k],v[1:k],Cki[k,1:k])
        v[k+2] = -v[k] - Sumuvw2(x[1:k],y[1:k],u[1:k],v[1:k],Cki[k,1:k])
    end
    
    return x,y,u,v
end

Talor (generic function with 1 method)

In [58]:
function Iteration(x,y,u,v,Cki)
    
    for st in 1:Times
    
        x,y,u,v = Talor(x,y,u,v,Cki)
        
        x[1] = sum(x[1:end].*Dmulti[1:end])
        y[1] = sum(y[1:end].*Dmulti[1:end])
        x[2] = sum(x[2:end].*Dmulti[1:end-1])
        y[2] = sum(y[2:end].*Dmulti[1:end-1])
        
        u[1] = sum(u[1:end].*Dmulti[1:end])
        v[1] = sum(v[1:end].*Dmulti[1:end])
        u[2] = sum(u[2:end].*Dmulti[1:end-1])
        v[2] = sum(v[2:end].*Dmulti[1:end-1])
    
        Lorenz[st,:] = [x[1],y[1]] 
        Lorenzf[st,:] = convert.(Float32,Lorenz[st,:])
        
        Ep[st] = (log10(abs(u[1]))+log10(abs(v[1])))/2 
      
        if mod(st,1000) == 0
            println(st,") ","time=",convert(Float16,st*steps()),": ",convert(Float16,Ep[st])," ",Lorenzf[st,:])
        end
    end
    
    return HH,Ep
    
end

Iteration (generic function with 1 method)

In [59]:
Times = 500000;      

x = Array{BigFloat}(undef,order())
y = Array{BigFloat}(undef,order())
u = Array{BigFloat}(undef,order())
v = Array{BigFloat}(undef,order())
Lorenz = Array{BigFloat}(undef,Times,2);
HH = Array{BigFloat}(undef,Times,2);
Ep = Array{BigFloat}(undef,Times,1);
Lorenzf = Array{Float32}(undef,Times,2);
Dmulti = Array{BigFloat}(undef,1,order());
Dmulti2 = Array{BigFloat}(undef,1,order()-1);
Cki = Array{BigFloat}(undef,order()-1,order()-1);

x[1] = BigFloat(14)/BigFloat(25); 
y[1] = BigFloat(0); 
x[2] = BigFloat(0); 
y[2] = BigFloat(0); 

mep = BigFloat(10)^BigFloat(-270)
u[1] = mep
v[1] = mep
u[2] = mep 
v[2] = mep

Cki = DJCh();
Dmulti = multi();

In [60]:
HH,Ep = Iteration(x,y,u,v,Cki);

1000) time=10.0: -269.8 Float32[-0.5818377, -0.24558878]
2000) time=20.0: -269.8 Float32[-0.7143643, -0.3738459]
3000) time=30.0: -267.8 Float32[-0.2219462, -0.0062423465]
4000) time=40.0: -268.2 Float32[0.29676586, -0.20299834]
5000) time=50.0: -268.0 Float32[-0.3666558, 0.19905551]
6000) time=60.0: -267.8 Float32[0.5017536, -0.3715834]
7000) time=70.0: -267.2 Float32[0.7139899, -0.44272265]
8000) time=80.0: -266.8 Float32[0.5886021, -0.396123]
9000) time=90.0: -265.5 Float32[-0.05946255, -0.0004932361]
10000) time=100.0: -265.5 Float32[0.009642523, -0.15411629]
11000) time=110.0: -264.8 Float32[0.21881688, -0.45289838]
12000) time=120.0: -264.5 Float32[-0.015478798, 0.35850307]
13000) time=130.0: -263.8 Float32[0.24502575, -0.12333115]
14000) time=140.0: -263.0 Float32[-0.61417526, -0.45333308]
15000) time=150.0: -262.8 Float32[-0.4043973, -0.33347794]
16000) time=160.0: -263.0 Float32[0.36681488, 0.31164262]
17000) time=170.0: -262.8 Float32[-0.29791772, -0.049737778]
18000) time=18

In [61]:
using Plots; 
plot(1:Times,Ep[1:end])

In [62]:
#write
function Wfile(AT,BE,Times)
#change name--------------------------------------------
    XLSX.openxlsx("CNEP_HH.xlsx", mode="w") do xf
#-------------------------------------------------------
        sheet = xf[1]
        XLSX.rename!(sheet, "new_sheet")
#change location----------------------------------------
        sheet["A1"] = "T"
        sheet["B1"] = "Ep"
        sheet["A2",dim=1] = AT[1:end]
        sheet["B2",dim=1] = BE[1:end]
#-------------------------------------------------------
    end
end
#-----------------------------------------------------------------------------
using XLSX
#time-----------------------------------------------------
AT=Array{Float32}(undef,Times)
for i in 1:Times
    AT[i]=i*steps()
end
#time-----------------------------------------------------
BE=Ep[1:end];
#--------------------------------------------------------
Wfile(AT,BE,Times);

In [63]:
sk = 0
sn = 0
for i in range(10000,Times,step=500)
    sk = sk + (Ep[i]-Ep[1])/((i-1)*steps())
    sn = sn + 1
end
sk/sn

0.044944474042410971424599362966496140747392287022607257136082681848055502584614071474582673643522664207736760625308256288514774599579009755446742509821267444402004786520268161933342099392210454211677795520275302203